In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
import shapely
import geopandas as gpd

print('Libraries imported.')

usage: conda [-h] [-V] command ...
conda: error: unrecognized arguments: # uncomment this line if you haven't completed the Foursquare API lab
usage: conda [-h] [-V] command ...
conda: error: unrecognized arguments: # uncomment this line if you haven't completed the Foursquare API lab


Libraries imported.


In [2]:
#geojson data for Houston is taken from Houston Open Poartal https://cohgis-mycity.opendata.arcgis.com/
with open('Super_Neighborhoods.geojson') as json_data:
    houston_data = json.load(json_data)
    

In [3]:
neighborhoods_data = houston_data['features']

In [4]:
neighborhoods_data[2]

{'type': 'Feature',
 'properties': {'OBJECTID': 3,
  'PERIMETER': 39256.388,
  'POLYID': 61,
  'SNBNAME': 'DOWNTOWN',
  'cohgisCOHG': 0,
  'cohgisCO_1': 0,
  'COUNCIL_AC': None,
  'RECOGNITIO': None,
  'SnbrInfoUR': 'http://www.houstontx.gov/superneighborhoods/61.html',
  'WeCan': None,
  'Top10': None},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[-95.34735199664924, 29.76623943247703],
    [-95.34853182037625, 29.765589772133367],
    [-95.34902614148137, 29.765303345234784],
    [-95.3493229279346, 29.764874999053042],
    [-95.34942640553459, 29.764605089834884],
    [-95.34943223496022, 29.76404586290133],
    [-95.34949334332292, 29.76282334475156],
    [-95.34950445785765, 29.76227062445713],
    [-95.34951553410444, 29.761674912425086],
    [-95.34945673697302, 29.76140144140779],
    [-95.34945519081768, 29.76062981397426],
    [-95.34945359396444, 29.759771517692794],
    [-95.34953522661964, 29.759671252349282],
    [-95.34956602752548, 29.758987004326332],
    [-95.

In [5]:
test=gpd.read_file("Super_Neighborhoods.geojson")
test.head(2)


OBJECTID  PERIMETER  POLYID      SNBNAME  cohgisCOHG  cohgisCO_1  \
0         1  16572.025      60  FOURTH WARD           0           0   
1         2  43118.770      63  SECOND WARD           0           0   

  COUNCIL_AC           RECOGNITIO  \
0       None                 None   
1        Yes  2008-05-13T00:00:00   

                                          SnbrInfoUR WeCan Top10  \
0  http://www.houstontx.gov/superneighborhoods/60...     Y  None   
1  http://www.houstontx.gov/superneighborhoods/63...     Y     Y   

                                            geometry  
0  POLYGON ((-95.3858120191703 29.76157948522658,...  
1  POLYGON ((-95.32015067938119 29.75615512902489...

In [6]:
#area in km/sqr*10^-10
test["area"] = test['geometry'].area/10**6*1000000000
test["Latitude"] = test['geometry'].centroid.x
test["Longitude"] = test['geometry'].centroid.y
#test["ZIP"]=test['ZIP_CODE']
test.head(5)
b=test.loc[test['SNBNAME'] == 'DOWNTOWN']
print(b)

   OBJECTID  PERIMETER  POLYID   SNBNAME  cohgisCOHG  cohgisCO_1 COUNCIL_AC  \
2         3  39256.388      61  DOWNTOWN           0           0       None   

  RECOGNITIO                                         SnbrInfoUR WeCan Top10  \
2       None  http://www.houstontx.gov/superneighborhoods/61...  None  None   

                                            geometry      area   Latitude  \
2  POLYGON ((-95.34735199664924 29.76623943247703...  0.654376 -95.359096   

   Longitude  
2  29.756689  


In [7]:
# ‘BuGn’, ‘BuPu’, ‘GnBu’, ‘OrRd’, ‘PuBu’, ‘PuBuGn’, ‘PuRd’, ‘RdPu’, ‘YlGn’, ‘YlGnBu’, ‘YlOrBr’, and ‘YlOrRd’.

In [9]:
map =folium.Map(location=[29.6196787, -95.6349463], zoom_start=8)

map.choropleth(geo_data=houston_data, data=test,
             columns=['OBJECTID', 'area'],
            # columns=['SQ', 'ZIP_CODE'],  
             key_on='feature.properties.OBJECTID',
             #key_on=houston_data_new.ZIP_CODE,  
             fill_color='PuRd', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Houston SuperNeighborhoods by Area')
folium.LayerControl().add_to(map)
map

In [10]:
zip=pd.read_csv('Census_2010_By_SuperNeighborhood.csv')
#zip data for Houston is taken from Houston Open Poartal https://cohgis-mycity.opendata.arcgis.com/

In [10]:
zip.head(100)

OBJECTID  SUM_POP100  SUM_HU100  SUM_TotPop  SUM_HispPop  SUM_NonHispPop  \
0          1        3881       2104        3881          711            3170   
1          2       13471       5120       13471        10603            2868   
2          3       16716       3664       16716         3266           13450   
3          4        2497       1133        2497          603            1894   
4          5       49277      31563       49277         7311           41966   
5          6       33973      15192       33973        15914           18059   
6          7       22317       7411       22317        15338            6979   
7          8       49757      17530       49757        34780           14977   
8          9       54978      28365       54978        12827           42151   
9         10       26285      14911       26285         7890           18395   
10        11       19823       8609       19823         8625           11198   
11        12       17164       5289       17164        16284             880   
12        13        3141       1350        3141          780            2361   
13        14       26963       9012       26963        19881            7082   
14        15       11715       6264       11715         4358            7357   
15        16       40865      21257       40865        15936           24929   
16        17        9527       4413        9527         2277            7250   
17        18        3503       1282        3503         1586            1917   
18        19       26831       9664       26831        22331            4500   
19        20       25564       9841       25564        16669            8895   
20        21       19728       8023       19728         9955            9773   
21        22        3135        865        3135         2109            1026   
22        23       28081       9499       28081        20828            7253   
23        24        2526        877        2526         1760             766   
24        25        4285       1732        4285          785            3500   
25        26        8954       3066        8954         6827            2127   
26        27       13388       5550       13388         6129            7259   
27        28       41561      19024       41561        17504           24057   
28        29       17020       6929       17020         4619           12401   
29        30        3143        887        3143         2113            1030   
30        31       27897       8692       27897        20402            7495   
31        32       19958       6799       19958         6860           13098   
32        33       24465       9288       24465         4782           19683   
33        34       58830      18327       58830        48613           10217   
34        35        4362       1268        4362         2971            1391   
35        36       20160       7650       20160         4125           16035   
36        37        7020       4283        7020         1940            5080   
37        38       42793      18633       42793        27769           15024   
38        39       10209       3641       10209         3813            6396   
39        40       59484      24317       59484         7093           52391   
40        41       14529       5253       14529         2586           11943   
41        42       13513       6479       13513         7488            6025   
42        43        5029       1709        5029         2465            2564   
43        44       75724      30285       75724        43244           32480   
44        45       18938       8296       18938        12383            6555   
45        46       34520      11069       34520        11094           23426   
46        47        2896       1145        2896         1728            1168   
47        48       54434      19643       54434        29579           24855   
48        49       18941       8041       18941         1600           17341   
49  

In [12]:
map =folium.Map(location=[29.6196787, -95.6349463], zoom_start=8)

map.choropleth(geo_data=houston_data, data=zip,
             columns=['OBJECTID', 'SUM_TotHousing'],
            # columns=['SQ', 'ZIP_CODE'],  
             key_on='feature.properties.OBJECTID',
             #key_on=houston_data_new.ZIP_CODE,  
             fill_color='GnBu', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Per capita income')
folium.LayerControl().add_to(map)
map

## Houston Food Project

In [79]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 
CLIENT_SECRET:


In [14]:
test_latitude=test['Longitude'][5]
test_longitude=test['Latitude'][5]
print(test_latitude,test_longitude)

#neighborhood_latitude=29.643886 
#neighborhood_longitude=-95.65205 

neighborhood_latitude=test_latitude
neighborhood_longitude=test_longitude

29.874411437359978 -95.48118309070259


In [15]:
"""
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius
 # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL
 
"""


"\nLIMIT = 100 # limit of number of venues returned by Foursquare API\n\nradius = 500 # define radius\n # create URL\nurl = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(\n    CLIENT_ID, \n    CLIENT_SECRET, \n    VERSION, \n    neighborhood_latitude, \n    neighborhood_longitude, \n    radius, \n    LIMIT)\nurl # display URL\n \n"

In [16]:
#search for certain categories
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 1500 # define radius
##All food
categoryId='4d4b7105d754a06374d81259' 

 # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT,
    categoryId
)
url # display URL
 



'https://api.foursquare.com/v2/venues/explore?&client_id=HKJI0CCM152WSO45MDDDA4AX0ITKZRAIX44U1KU1FPX3BPUM&client_secret=BIBJ3KDBRNNPRRN52FUFOENV4JBFNZWDJJAHMW5LFTU2SNQM&v=20180605&ll=29.874411437359978,-95.48118309070259&radius=1500&limit=100&categoryId=4d4b7105d754a06374d81259'

In [17]:
results = requests.get(url).json()
results
#headerLocation

{'meta': {'code': 200, 'requestId': '5c0f65baf594df18fe47b4a4'},
 'response': {'headerLocation': 'Greater Inwood',
  'headerFullLocation': 'Greater Inwood, Houston',
  'headerLocationGranularity': 'neighborhood',
  'query': 'food',
  'totalResults': 17,
  'suggestedBounds': {'ne': {'lat': 29.887911450859992,
    'lng': -95.46564335171354},
   'sw': {'lat': 29.860911423859964, 'lng': -95.49672282969163}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c0e7e8796fc9521b3bac0cb',
       'name': 'Cajun Town Café',
       'location': {'address': '6476 W Little York Rd',
        'crossStreet': 'Bingle',
        'lat': 29.86660775254566,
        'lng': -95.48630718673724,
        'labeledLatLngs': [{'label': 'display',
          'lat': 29.86660775254566,
          'lng': -95.4

In [18]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [19]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head(15)

name                 categories        lat  \
0              Cajun Town Café  Cajun / Creole Restaurant  29.866608   
1   Taqueria Rancho El Jalisco         Mexican Restaurant  29.867247   
2              Jack in the Box       Fast Food Restaurant  29.865416   
3                       SUBWAY             Sandwich Place  29.863399   
4               Domino's Pizza                Pizza Place  29.866450   
5                     Wingstop                Wings Joint  29.867872   
6               SONIC Drive In       Fast Food Restaurant  29.867498   
7             Church's Chicken        Fried Chicken Joint  29.884993   
8         Little Caesars Pizza                Pizza Place  29.864395   
9         Hartz Chicken Buffet       Fast Food Restaurant  29.869125   
10     Mekong Oriental Cuisine                       Food  29.884721   
11      T and L Seafood Market                       Food  29.884881   
12          Shipleys Doughnuts                 Donut Shop  29.865827   
13              Bimbo Bakeries                     Bakery  29.863199   
14                   Pizza Hut                Pizza Place  29.885666   

          lng  
0  -95.486307  
1  -95.487283  
2  -95.486476  
3  -95.474830  
4  -95.472350  
5  -95.471529  
6  -95.488656  
7  -95.474538  
8  -95.473792  
9  -95.489177  
10 -95.480084  
11 -95.479281  
12 -95.472515  
13 -95.484100  
14 -95.473655

In [20]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

17 venues were returned by Foursquare.


In [21]:
#For All ZIPs in Houston

In [22]:
for i in range(0,test['Longitude'].size):
    test_latitude=test['Longitude'][i]
    test_longitude=test['Latitude'][i]
    test_SNBNAMEP=test['SNBNAME'][i]
    #print(test_latitude,test_longitude,test_ZIP)
    #print()

In [23]:
def getNearbyVenues2(ZIP, lat, lng, radius=1000):
    
#    venues_list=[]
    print(ZIP)

    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        lng, 
        radius, 
        LIMIT,
        categoryId)
    #print(url)
   
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    #results = requests.get(url).json()
    nearby_venues = json_normalize(venues) # flatten JSON
    # filter columns
    filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
    nearby_venues =nearby_venues.loc[:, filtered_columns]
    # filter the category for each row
    nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)
    # clean columns
    nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]
    #print(nearby_venues.head())
    


    
    # return only relevant information for each nearby venue
    venues_list.append([(
        ZIP, 
        lat, 
        lng, 
        v['venue']['name'], 
        v['venue']['location']['lat'], 
        v['venue']['location']['lng'],  
        v['venue']['categories'][0]['name']) for v in results])
    #print(venues_list)

 

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['ZIP', 
                  'ZIP Latitude', 
                  'ZIP Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    #print(nearby_venues)
    return(nearby_venues)


In [24]:
venues_list=[]
for i in range(1,test['Longitude'].size):    
#for i in range(0,test['Longitude'].size):
    test_latitude=test['Latitude'][i]
    test_longitude=test['Longitude'][i]
    test_ZIP=test['SNBNAME'][i]
    #print(test_latitude,test_longitude,test_ZIP)
    #print()
    houston_venues = getNearbyVenues2(test_ZIP,
                                   test_longitude,
                                   test_latitude
                                  )

SECOND WARD
DOWNTOWN
CLINTON PARK TRI-COMMUNITY
GREATER UPTOWN
GREATER INWOOD
GREATER HOBBY AREA
GOLFCREST / BELLFORT / REVEILLE
ELDRIDGE / WEST OAKS
WASHINGTON AVENUE COALITION / MEMORIAL PARK
GREATER FIFTH WARD
DENVER HARBOR / PORT HOUSTON
PLEASANTVILLE AREA
NORTHSHORE
LAZYBROOK / TIMBERGROVE
GREATER HEIGHTS
KASHMERE GARDENS
MINNETEX
NEAR NORTHSIDE
SPRING BRANCH EAST
SPRING BRANCH NORTH
EL DORADO / OATES PRAIRIE
SPRING BRANCH CENTRAL
HUNTERWOOD
SETTEGAST
LANGWOOD
INDEPENDENCE HEIGHTS
CENTRAL NORTHWEST
TRINITY / HOUSTON GARDENS
CARVERDALE
EASTEX - JENSEN AREA
EAST HOUSTON
ACRES HOME
NORTHSIDE/NORTHLINE
HIDDEN VALLEY
EAST LITTLE YORK / HOMESTEAD
WILLOWBROOK
GREATER GREENSPOINT
IAH / AIRPORT AREA
KINGWOOD AREA
LAKE HOUSTON
FAIRBANKS / NORTHWEST CROSSING
WESTBRANCH
SHARPSTOWN
WESTWOOD
FORT BEND HOUSTON
FONDREN GARDENS
SOUTH BELT / ELLINGTON
SOUTH ACRES / CRESTMONT PARK
BRAYS OAKS
CENTRAL SOUTHWEST
SUNNYSIDE
ALIEF
PECAN PARK
CLEAR LAKE
WESTBURY
WILLOW MEADOWS / WILLOWBEND AREA
BRAEBURN
SO

In [25]:
houston_venues.shape

(1456, 7)

In [26]:
houston_venues.head()

ZIP  ZIP Latitude  ZIP Longitude  \
0  SECOND WARD     29.750962     -95.327939   
1  SECOND WARD     29.750962     -95.327939   
2  SECOND WARD     29.750962     -95.327939   
3  SECOND WARD     29.750962     -95.327939   
4  SECOND WARD     29.750962     -95.327939   

                                Venue  Venue Latitude  Venue Longitude  \
0  "La Silla" Pollos asados al carbon       29.748268       -95.327063   
1                Refresqueria Tampico       29.743250       -95.326179   
2                     Jack in the Box       29.755628       -95.335421   
3                   Papa John's Pizza       29.747823       -95.327195   
4                          McDonald's       29.751435       -95.322766   

         Venue Category  
0    Mexican Restaurant  
1           Snack Place  
2  Fast Food Restaurant  
3           Pizza Place  
4  Fast Food Restaurant

In [27]:
 houston_venues.groupby('ZIP').count()

ZIP Latitude  ZIP Longitude  \
ZIP                                                                        
ACRES HOME                                              6              6   
AFTON OAKS / RIVER OAKS AREA                            9              9   
ALIEF                                                   4              4   
ASTRODOME AREA                                         22             22   
BRAEBURN                                                7              7   
BRAESWOOD                                               6              6   
BRAYS OAKS                                              9              9   
BRIAR FOREST                                           14             14   
CARVERDALE                                              7              7   
CENTRAL NORTHWEST                                       7              7   
CENTRAL SOUTHWEST                                       5              5   
CLEAR LAKE                                              4              4   
CLINTON PARK TRI-COMMUNITY                              2              2   
DENVER HARBOR / PORT HOUSTON                            3              3   
DOWNTOWN                                              100            100   
EAST HOUSTON                                           10             10   
EAST LITTLE YORK / HOMESTEAD                            3              3   
EASTEX - JENSEN AREA                                   12             12   
EDGEBROOK AREA                                          8              8   
FAIRBANKS / NORTHWEST CROSSING                         36             36   
FONDREN GARDENS                                         9              9   
FORT BEND HOUSTON                                       4              4   
GOLFCREST / BELLFORT / REVEILLE                        14             14   
GREATER EASTWOOD                                       15             15   
GREATER FIFTH WARD                                      7              7   
GREATER GREENSPOINT                                    28             28   
GREATER HEIGHTS                                        32             32   
GREATER HOBBY AREA                                      5              5   
GREATER INWOOD                                          5              5   
GREATER OST / SOUTH UNION                               5              5   
GREATER THIRD WARD                                     25             25   
GREATER UPTOWN                                         24             24   
GREENWAY / UPPER KIRBY AREA                            84             84   
GULFGATE RIVERVIEW / PINE VALLEY                       23             23   
GULFTON                                                38             38   
HARRISBURG / MANCHESTER                                 3              3   
HIDDEN VALLEY                                           9              9   
INDEPENDENCE HEIGHTS                                    5              5   
KASHMERE GARDENS                                        8              8   
KINGWOOD AREA                                           4              4   
LAKE HOUSTON                                            1              1   
LANGWOOD                                               11             11   
LAWNDALE / WAYSIDE                                      7              7   
LAZYBROOK / TIMBERGROVE                                18             18   
MACGREGOR                                               7              7   
MAGNOLIA PARK                                          20             20   
MEADOWBROOK / ALLENDALE                                 4              4   
MEDICAL CENTER AREA                                    39             39   
MEMORIAL                                               14             14   
MEYERLAND AREA                                         11             11   
MID WEST                                               59             59   
MIDTOWN          

In [28]:
print('There are {} uniques categories.'.format(len(houston_venues['Venue Category'].unique()))) 

There are 87 uniques categories.


In [30]:
# one hot encoding
houston_onehot = pd.get_dummies(houston_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
houston_onehot['ZIP'] = houston_venues['ZIP'] 

# move neighborhood column to the first column
fixed_columns = [houston_onehot.columns[-1]] + list(houston_onehot.columns[:-1])
houston_onehot = houston_onehot[fixed_columns]

houston_onehot.head()

ZIP  African Restaurant  American Restaurant  \
0  SECOND WARD                   0                    0   
1  SECOND WARD                   0                    0   
2  SECOND WARD                   0                    0   
3  SECOND WARD                   0                    0   
4  SECOND WARD                   0                    0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           0       0   
1                       0                 0          0           0       0   
2                       0                 0          0           0       0   
3                       0                 0          0           0       0   
4                       0                 0          0           0       0   

   Bistro  Brazilian Restaurant  Breakfast Spot  Buffet  Burger Joint  \
0       0                     0               0       0             0   
1       0                     0               0       0             0   
2       0                     0               0       0             0   
3       0                     0               0       0             0   
4       0                     0               0       0             0   

   Burrito Place  Cafeteria  Café  Cajun / Creole Restaurant  \
0              0          0     0                          0   
1              0          0     0                          0   
2              0          0     0                          0   
3              0          0     0                          0   
4              0          0     0                          0   

   Caribbean Restaurant  Chinese Restaurant  Churrascaria  \
0                     0                   0             0   
1                     0                   0             0   
2                     0                   0             0   
3                     0                   0             0   
4                     0                   0             0   

   Comfort Food Restaurant  Creperie  Cuban Restaurant  Deli / Bodega  \
0                        0         0                 0              0   
1                        0         0                 0              0   
2                        0         0                 0              0   
3                        0         0                 0              0   
4                        0         0                 0              0   

   Dim Sum Restaurant  Diner  Doner Restaurant  Donut Shop  \
0                   0      0                 0           0   
1                   0      0                 0           0   
2                   0      0                 0           0   
3                   0      0                 0           0   
4                   0      0                 0           0   

   Dumpling Restaurant  Eastern European Restaurant  Ethiopian Restaurant  \
0                    0                            0                     0   
1                    0                            0                     0   
2                    0                            0                     0   
3                    0                            0                     0   
4                    0                            0                     0   

   Falafel Restaurant  Fast Food Restaurant  Filipino Restaurant  Food  \
0                   0                     0                    0     0   
1                   0                     0                    0     0   
2                   0                     1                    0     0   
3                   0                     0                    0     0   
4                   0                     1                    0     0   

   Food Court  Food Stand  Food Truck  French Restaurant  Fried Chicken Joint  \
0           0           0           0                  0                    0   
1           0           0           0                  0                    0   
2           0           0        

In [31]:
houston_onehot.shape

(1456, 88)

In [32]:
houston_grouped = houston_onehot.groupby('ZIP').mean().reset_index()
houston_grouped.head()


ZIP  African Restaurant  American Restaurant  \
0                    ACRES HOME                 0.0             0.000000   
1  AFTON OAKS / RIVER OAKS AREA                 0.0             0.111111   
2                         ALIEF                 0.0             0.250000   
3                ASTRODOME AREA                 0.0             0.045455   
4                      BRAEBURN                 0.0             0.142857   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                     0.0               0.0        0.0         0.0    0.00   
1                     0.0               0.0        0.0         0.0    0.00   
2                     0.0               0.0        0.0         0.0    0.25   
3                     0.0               0.0        0.0         0.0    0.00   
4                     0.0               0.0        0.0         0.0    0.00   

   Bistro  Brazilian Restaurant  Breakfast Spot  Buffet  Burger Joint  \
0     0.0                   0.0             0.0     0.0      0.333333   
1     0.0                   0.0             0.0     0.0      0.111111   
2     0.0                   0.0             0.0     0.0      0.000000   
3     0.0                   0.0             0.0     0.0      0.000000   
4     0.0                   0.0             0.0     0.0      0.000000   

   Burrito Place  Cafeteria      Café  Cajun / Creole Restaurant  \
0            0.0        0.0  0.000000                       0.00   
1            0.0        0.0  0.111111                       0.00   
2            0.0        0.0  0.000000                       0.25   
3            0.0        0.0  0.045455                       0.00   
4            0.0        0.0  0.000000                       0.00   

   Caribbean Restaurant  Chinese Restaurant  Churrascaria  \
0              0.000000            0.166667           0.0   
1              0.000000            0.000000           0.0   
2              0.000000            0.000000           0.0   
3              0.045455            0.090909           0.0   
4              0.142857            0.000000           0.0   

   Comfort Food Restaurant  Creperie  Cuban Restaurant  Deli / Bodega  \
0                      0.0       0.0               0.0       0.000000   
1                      0.0       0.0               0.0       0.000000   
2                      0.0       0.0               0.0       0.000000   
3                      0.0       0.0               0.0       0.090909   
4                      0.0       0.0               0.0       0.000000   

   Dim Sum Restaurant  Diner  Doner Restaurant  Donut Shop  \
0                 0.0    0.0               0.0    0.000000   
1                 0.0    0.0               0.0    0.111111   
2                 0.0    0.0               0.0    0.000000   
3                 0.0    0.0               0.0    0.000000   
4                 0.0    0.0               0.0    0.000000   

   Dumpling Restaurant  Eastern European Restaurant  Ethiopian Restaurant  \
0                  0.0                          0.0                   0.0   
1                  0.0                          0.0                   0.0   
2                  0.0                          0.0                   0.0   
3                  0.0                          0.0                   0.0   
4                  0.0                          0.0                   0.0   

   Falafel Restaurant  Fast Food Restaurant  Filipino Restaurant      Food  \
0                 0.0              0.000000                  0.0  0.000000   
1                 0.0              0.111111                  0.0  0.000000   
2                 0.0              0.000000                  0.0  0.250000   
3                 0.0              0.000000                  0.0  0.000000   
4                 0.0              0.142857                  0.0  0.285714   

   Food Court  Food Stand  Food Truck  French Restaurant  Fried Chicken Joint  \
0         0.0    0.166667    0.000000                0.0      

In [33]:
#Let's print each neighborhood along with the top 5 most common venues
num_top_venues = 3

for hood in houston_grouped['ZIP']:
    hood2=str(hood)
    print("----"+hood2+"----")
    temp = houston_grouped[houston_grouped['ZIP'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ACRES HOME----
                             venue  freq
0  Southern / Soul Food Restaurant  0.33
1                     Burger Joint  0.33
2               Chinese Restaurant  0.17


----AFTON OAKS / RIVER OAKS AREA----
                             venue  freq
0  Southern / Soul Food Restaurant  0.22
1                       Donut Shop  0.11
2                             Café  0.11


----ALIEF----
                 venue  freq
0                 Food  0.25
1  American Restaurant  0.25
2               Bakery  0.25


----ASTRODOME AREA----
               venue  freq
0         Food Truck  0.18
1  Indian Restaurant  0.14
2         Restaurant  0.09


----BRAEBURN----
                 venue  freq
0                 Food  0.29
1  American Restaurant  0.14
2       Sandwich Place  0.14


----BRAESWOOD----
            venue  freq
0      Steakhouse  0.17
1            Food  0.17
2  Sandwich Place  0.17


----BRAYS OAKS----
                  venue  freq
0  Fast Food Restaurant  0.22
1           Pizza

                      venue  freq
0        Mexican Restaurant   1.0
1        African Restaurant   0.0
2  Mediterranean Restaurant   0.0


----SECOND WARD----
                  venue  freq
0            Taco Place  0.15
1  Fast Food Restaurant  0.15
2          Burger Joint  0.15


----SETTEGAST----
                 venue  freq
0                 Food  0.67
1  American Restaurant  0.33
2     Hunan Restaurant  0.00


----SHARPSTOWN----
                   venue  freq
0                   Food  0.08
1  Vietnamese Restaurant  0.08
2            Pizza Place  0.08


----SOUTH ACRES / CRESTMONT PARK----
                  venue  freq
0  Fast Food Restaurant   0.4
1    Seafood Restaurant   0.2
2                Bakery   0.2


----SOUTH BELT / ELLINGTON----
                venue  freq
0  Mexican Restaurant   0.4
1        Burger Joint   0.2
2  Tex-Mex Restaurant   0.2


----SOUTH MAIN----
                  venue  freq
0  Fast Food Restaurant  0.22
1                  Food  0.11
2        Breakfast Spot  0

In [34]:
#let's put that into a pandas dataframe
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [35]:
#Now let's create the new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 3

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['ZIP']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['ZIP'] = houston_grouped['ZIP']

for ind in np.arange(houston_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(houston_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

ZIP  \
0                                    ACRES HOME   
1                  AFTON OAKS / RIVER OAKS AREA   
2                                         ALIEF   
3                                ASTRODOME AREA   
4                                      BRAEBURN   
5                                     BRAESWOOD   
6                                    BRAYS OAKS   
7                                  BRIAR FOREST   
8                                    CARVERDALE   
9                             CENTRAL NORTHWEST   
10                            CENTRAL SOUTHWEST   
11                                   CLEAR LAKE   
12                   CLINTON PARK TRI-COMMUNITY   
13                 DENVER HARBOR / PORT HOUSTON   
14                                     DOWNTOWN   
15                                 EAST HOUSTON   
16                 EAST LITTLE YORK / HOMESTEAD   
17                         EASTEX - JENSEN AREA   
18                               EDGEBROOK AREA   
19               FAIRBANKS / NORTHWEST CROSSING   
20                              FONDREN GARDENS   
21                            FORT BEND HOUSTON   
22              GOLFCREST / BELLFORT / REVEILLE   
23                             GREATER EASTWOOD   
24                           GREATER FIFTH WARD   
25                          GREATER GREENSPOINT   
26                              GREATER HEIGHTS   
27                           GREATER HOBBY AREA   
28                               GREATER INWOOD   
29                    GREATER OST / SOUTH UNION   
30                           GREATER THIRD WARD   
31                               GREATER UPTOWN   
32                  GREENWAY / UPPER KIRBY AREA   
33             GULFGATE RIVERVIEW / PINE VALLEY   
34                                      GULFTON   
35                      HARRISBURG / MANCHESTER   
36                                HIDDEN VALLEY   
37                         INDEPENDENCE HEIGHTS   
38                             KASHMERE GARDENS   
39                                KINGWOOD AREA   
40                                 LAKE HOUSTON   
41                                     LANGWOOD   
42                           LAWNDALE / WAYSIDE   
43                      LAZYBROOK / TIMBERGROVE   
44                                    MACGREGOR   
45                                MAGNOLIA PARK   
46                      MEADOWBROOK / ALLENDALE   
47                          MEDICAL CENTER AREA   
48                                     MEMORIAL   
49                               MEYERLAND AREA   
50                                     MID WEST   
51                                      MIDTOWN   
52                                  MUSEUM PARK   
53                               NEAR NORTHSIDE   
54                          NEARTOWN - MONTROSE   
55                                   NORTHSHORE   
56                          NORTHSIDE/NORTHLINE   
57                                   PARK PLACE   
58                                   PECAN PARK   
59                           PLEASANTVILLE AREA   
60                                  SECOND WARD   
61                                    SETTEGAST   
62                                   SHARPSTOWN   
63                 SOUTH ACRES / CRESTMONT PARK   
64                       SOUTH BELT / ELLINGTON   
65                                   SOUTH MAIN   
66                                   SOUTH PARK   
67                        SPRING BRANCH CENTRAL   
68                           SPRING BRANCH EAST   
69                          SPRING BRANCH NORTH   
70                           SPRING BRANCH WEST   
71                                    SUNNYSIDE   
72                    TRINITY / HOUSTON GARDENS   
73                             UNIVERSITY PLACE   
74  WASHINGTON AVENUE COALITION / MEMORIAL PARK   
75                                   WESTBRANCH   
76                                     WESTBURY   
77                                    WESTCHASE   
78             

In [36]:
neighborhoods_venues_sorted.rename(columns={'ZIP':'SNBNAME'},inplace=True)

neighborhoods_venues_sorted.head(2)


SNBNAME            1st Most Common Venue  \
0                    ACRES HOME                     Burger Joint   
1  AFTON OAKS / RIVER OAKS AREA  Southern / Soul Food Restaurant   

             2nd Most Common Venue 3rd Most Common Venue  
0  Southern / Soul Food Restaurant    Chinese Restaurant  
1                     Burger Joint   American Restaurant

In [37]:
type(test)
test2=pd.DataFrame(test)
type(test2)
test2.head()
houston_geo=test2.drop(['OBJECTID','PERIMETER', 'POLYID','cohgisCOHG','COUNCIL_AC','cohgisCO_1','RECOGNITIO','SnbrInfoUR','WeCan','Top10','geometry','area'], axis=1)
houston_geo

SNBNAME   Latitude  Longitude
0                                   FOURTH WARD -95.380766  29.757116
1                                   SECOND WARD -95.327939  29.750962
2                                      DOWNTOWN -95.359096  29.756689
3                    CLINTON PARK TRI-COMMUNITY -95.262714  29.748397
4                                GREATER UPTOWN -95.475614  29.756552
5                                GREATER INWOOD -95.481183  29.874411
6                            GREATER HOBBY AREA -95.278045  29.629654
7               GOLFCREST / BELLFORT / REVEILLE -95.294512  29.672904
8                          ELDRIDGE / WEST OAKS -95.667038  29.741726
9   WASHINGTON AVENUE COALITION / MEMORIAL PARK -95.418402  29.771182
10                           GREATER FIFTH WARD -95.330012  29.777657
11                 DENVER HARBOR / PORT HOUSTON -95.293949  29.766369
12                           PLEASANTVILLE AREA -95.275180  29.777972
13                                   NORTHSHORE -95.220746  29.779982
14                      LAZYBROOK / TIMBERGROVE -95.437531  29.797797
15                              GREATER HEIGHTS -95.397350  29.797332
16                             KASHMERE GARDENS -95.322484  29.802721
17                                     MINNETEX -95.325820  29.615914
18                               NEAR NORTHSIDE -95.360912  29.796894
19                           SPRING BRANCH EAST -95.477236  29.802936
20                          SPRING BRANCH NORTH -95.543666  29.821121
21                    EL DORADO / OATES PRAIRIE -95.245986  29.805655
22                        SPRING BRANCH CENTRAL -95.514277  29.812867
23                                   HUNTERWOOD -95.215163  29.817515
24                                    SETTEGAST -95.279048  29.817209
25                                     LANGWOOD -95.490932  29.826409
26                         INDEPENDENCE HEIGHTS -95.396065  29.829166
27                            CENTRAL NORTHWEST -95.444859  29.829097
28                    TRINITY / HOUSTON GARDENS -95.308015  29.828119
29                                   CARVERDALE -95.550278  29.855090
30                         EASTEX - JENSEN AREA -95.342538  29.846523
31                                 EAST HOUSTON -95.257753  29.843108
32                                   ACRES HOME -95.436267  29.864097
33                          NORTHSIDE/NORTHLINE -95.381932  29.854133
34                                HIDDEN VALLEY -95.417324  29.891505
35                 EAST LITTLE YORK / HOMESTEAD -95.297036  29.871777
36                                  WILLOWBROOK -95.543023  29.953919
37                          GREATER GREENSPOINT -95.410059  29.940435
38                           IAH / AIRPORT AREA -95.323497  29.973156
39                                KINGWOOD AREA -95.198536  30.051070
40                                 LAKE HOUSTON -95.149110  29.983309
41               FAIRBANKS / NORTHWEST CROSSING -95.512603  29.849347
42                                   WESTBRANCH -95.559613  29.838073
43                                   SHARPSTOWN -95.524952  29.703853
44                                     WESTWOOD -95.550073  29.676080
45                            FORT BEND HOUSTON -95.486898  29.593609
46                              FONDREN GARDENS -95.503068  29.625244
47                       SOUTH BELT / ELLINGTON -95.205141  29.608477
48                 SOUTH ACRES / CRESTMONT PARK -95.358987  29.628829
49                                   BRAYS OAKS -95.525802  29.654755
50                            CENTRAL SOUTHWEST -95.432339  29.630323
51                                    SUNNYSIDE -95.367446  29.659005
52                                        ALIEF -95.586392  29.686317
53                                   PECAN PARK -95.287175  29.707712
54                                   CLEAR LAKE -95.134963  29.578395
55                                     WESTBURY -95.482300  29.653772
56             WILLOW MEADOWS / WILLOWBEND AREA -9

In [38]:
#zip.head(2)
SUM_TotHousing=zip.drop(['SUM_VAP_HawPac','SUM_VAP_NH_Oth','SUM_VAP_NHOneR','SUM_VAP_NH_Whi','SUM_VAP_NH_Bla','SUM_VAP_NH_AmI','SUM_VAP_NH_Asi','OBJECTID','SUM_NH_2orMore','SUM_VAP_TotPop','SUM_VAP_HispPo','SUM_VAP_NonHis','POLYID','Shapelen','Shapearea','SUM_VacantHU','SUM_OccHU','SUM_POP100','SUM_HU100', 'SUM_TotPop','SUM_HispPop','SUM_NonHispPop','SUM_NHOneRace','SUM_NH_White','SUM_NH_Black','SUM_NH_AmInd','SUM_NH_Asian','SUM_NH_HawPacI','SUM_NH_Other','SUM_VAP_NH_2or'], axis=1)
SUM_TotHousing.rename(columns={'Name':'SNBNAME'},inplace=True)
SUM_TotHousing

SUM_TotHousing                                      SNBNAME
0             2104                                  FOURTH WARD
1             5120                                  SECOND WARD
2             3664                                     DOWNTOWN
3             1133                   CLINTON PARK TRI-COMMUNITY
4            31563                               GREATER UPTOWN
5            15192                               GREATER INWOOD
6             7411                           GREATER HOBBY AREA
7            17530              GOLFCREST / BELLFORT / REVEILLE
8            28365                         ELDRIDGE / WEST OAKS
9            14911  WASHINGTON AVENUE COALITION / MEMORIAL PARK
10            8609                           GREATER FIFTH WARD
11            5289                 DENVER HARBOR / PORT HOUSTON
12            1350                           PLEASANTVILLE AREA
13            9012                                   NORTHSHORE
14            6264                     LAZY BROOK / TIMBERGROVE
15           21257                              GREATER HEIGHTS
16            4413                             KASHMERE GARDENS
17            1282                                     MINNETEX
18            9664                            NORTHSIDE VILLAGE
19            9841                           SPRING BRANCH EAST
20            8023                          SPRING BRANCH NORTH
21             865                    EL DORADO / OATES PRAIRIE
22            9499                        SPRING BRANCH CENTRAL
23             877                                   HUNTERWOOD
24            1732                                    SETTEGAST
25            3066                                     LANGWOOD
26            5550                         INDEPENDENCE HEIGHTS
27           19024                            CENTRAL NORTHWEST
28            6929                    TRINITY / HOUSTON GARDENS
29             887                                   CARVERDALE
30            8692                         EASTEX - JENSEN AREA
31            6799                                 EAST HOUSTON
32            9288                                   ACRES HOME
33           18327                          NORTHSIDE/NORTHLINE
34            1268                                HIDDEN VALLEY
35            7650                 EAST LITTLE YORK / HOMESTEAD
36            4283                                  WILLOWBROOK
37           18633                          GREATER GREENSPOINT
38            3641                           IAH / AIRPORT AREA
39           24317                                KINGWOOD AREA
40            5253                                 LAKE HOUSTON
41            6479               FAIRBANKS / NORTHWEST CROSSING
42            1709                                   WESTBRANCH
43           30285                                   SHARPSTOWN
44            8296                                     WESTWOOD
45           11069                          FORT BEND / HOUSTON
46            1145                              FONDREN GARDENS
47           19643                       SOUTH BELT / ELLINGTON
48            8041                 SOUTH ACRES / CRESTMONT PARK
49           25068                                   BRAYS OAKS
50           19004                            CENTRAL SOUTHWEST
51            8996                                    SUNNYSIDE
52           35498                                        ALIEF
53            5440                                   PECAN PARK
54           24182                                   CLEAR LAKE
55            8086                                     WESTBURY
56            5922             WILLOW MEADOWS / WILLOWBEND AREA
57            8216                                     BRAEBURN
58            4464                                   SOUTH MAIN
59            7345                                   SOUTH PARK
60           11311                               ASTRODOME AREA
61            8550                  

In [39]:
houston = neighborhoods_venues_sorted.join(SUM_TotHousing.set_index('SNBNAME'), on='SNBNAME')
houston.fillna(0)
houston 
#neighborhoods_venues_sorted.head()

SNBNAME  \
0                                    ACRES HOME   
1                  AFTON OAKS / RIVER OAKS AREA   
2                                         ALIEF   
3                                ASTRODOME AREA   
4                                      BRAEBURN   
5                                     BRAESWOOD   
6                                    BRAYS OAKS   
7                                  BRIAR FOREST   
8                                    CARVERDALE   
9                             CENTRAL NORTHWEST   
10                            CENTRAL SOUTHWEST   
11                                   CLEAR LAKE   
12                   CLINTON PARK TRI-COMMUNITY   
13                 DENVER HARBOR / PORT HOUSTON   
14                                     DOWNTOWN   
15                                 EAST HOUSTON   
16                 EAST LITTLE YORK / HOMESTEAD   
17                         EASTEX - JENSEN AREA   
18                               EDGEBROOK AREA   
19               FAIRBANKS / NORTHWEST CROSSING   
20                              FONDREN GARDENS   
21                            FORT BEND HOUSTON   
22              GOLFCREST / BELLFORT / REVEILLE   
23                             GREATER EASTWOOD   
24                           GREATER FIFTH WARD   
25                          GREATER GREENSPOINT   
26                              GREATER HEIGHTS   
27                           GREATER HOBBY AREA   
28                               GREATER INWOOD   
29                    GREATER OST / SOUTH UNION   
30                           GREATER THIRD WARD   
31                               GREATER UPTOWN   
32                  GREENWAY / UPPER KIRBY AREA   
33             GULFGATE RIVERVIEW / PINE VALLEY   
34                                      GULFTON   
35                      HARRISBURG / MANCHESTER   
36                                HIDDEN VALLEY   
37                         INDEPENDENCE HEIGHTS   
38                             KASHMERE GARDENS   
39                                KINGWOOD AREA   
40                                 LAKE HOUSTON   
41                                     LANGWOOD   
42                           LAWNDALE / WAYSIDE   
43                      LAZYBROOK / TIMBERGROVE   
44                                    MACGREGOR   
45                                MAGNOLIA PARK   
46                      MEADOWBROOK / ALLENDALE   
47                          MEDICAL CENTER AREA   
48                                     MEMORIAL   
49                               MEYERLAND AREA   
50                                     MID WEST   
51                                      MIDTOWN   
52                                  MUSEUM PARK   
53                               NEAR NORTHSIDE   
54                          NEARTOWN - MONTROSE   
55                                   NORTHSHORE   
56                          NORTHSIDE/NORTHLINE   
57                                   PARK PLACE   
58                                   PECAN PARK   
59                           PLEASANTVILLE AREA   
60                                  SECOND WARD   
61                                    SETTEGAST   
62                                   SHARPSTOWN   
63                 SOUTH ACRES / CRESTMONT PARK   
64                       SOUTH BELT / ELLINGTON   
65                                   SOUTH MAIN   
66                                   SOUTH PARK   
67                        SPRING BRANCH CENTRAL   
68                           SPRING BRANCH EAST   
69                          SPRING BRANCH NORTH   
70                           SPRING BRANCH WEST   
71                                    SUNNYSIDE   
72                    TRINITY / HOUSTON GARDENS   
73                             UNIVERSITY PLACE   
74  WASHINGTON AVENUE COALITION / MEMORIAL PARK   
75                                   WESTBRANCH   
76                                     WESTBURY   
77                                    WESTCHASE   
78         

In [40]:
houston_grouped.rename(columns={'ZIP':'SNBNAME'},inplace=True)
houston_housing=houston_grouped.join(SUM_TotHousing.set_index('SNBNAME'), on='SNBNAME')
houston_housing2=houston_housing.fillna(0)
houston_housing2

SNBNAME  African Restaurant  \
0                                    ACRES HOME                 0.0   
1                  AFTON OAKS / RIVER OAKS AREA                 0.0   
2                                         ALIEF                 0.0   
3                                ASTRODOME AREA                 0.0   
4                                      BRAEBURN                 0.0   
5                                     BRAESWOOD                 0.0   
6                                    BRAYS OAKS                 0.0   
7                                  BRIAR FOREST                 0.0   
8                                    CARVERDALE                 0.0   
9                             CENTRAL NORTHWEST                 0.0   
10                            CENTRAL SOUTHWEST                 0.0   
11                                   CLEAR LAKE                 0.0   
12                   CLINTON PARK TRI-COMMUNITY                 0.0   
13                 DENVER HARBOR / PORT HOUSTON                 0.0   
14                                     DOWNTOWN                 0.0   
15                                 EAST HOUSTON                 0.0   
16                 EAST LITTLE YORK / HOMESTEAD                 0.0   
17                         EASTEX - JENSEN AREA                 0.0   
18                               EDGEBROOK AREA                 0.0   
19               FAIRBANKS / NORTHWEST CROSSING                 0.0   
20                              FONDREN GARDENS                 0.0   
21                            FORT BEND HOUSTON                 0.0   
22              GOLFCREST / BELLFORT / REVEILLE                 0.0   
23                             GREATER EASTWOOD                 0.0   
24                           GREATER FIFTH WARD                 0.0   
25                          GREATER GREENSPOINT                 0.0   
26                              GREATER HEIGHTS                 0.0   
27                           GREATER HOBBY AREA                 0.0   
28                               GREATER INWOOD                 0.0   
29                    GREATER OST / SOUTH UNION                 0.0   
30                           GREATER THIRD WARD                 0.0   
31                               GREATER UPTOWN                 0.0   
32                  GREENWAY / UPPER KIRBY AREA                 0.0   
33             GULFGATE RIVERVIEW / PINE VALLEY                 0.0   
34                                      GULFTON                 0.0   
35                      HARRISBURG / MANCHESTER                 0.0   
36                                HIDDEN VALLEY                 0.0   
37                         INDEPENDENCE HEIGHTS                 0.0   
38                             KASHMERE GARDENS                 0.0   
39                                KINGWOOD AREA                 0.0   
40                                 LAKE HOUSTON                 0.0   
41                                     LANGWOOD                 0.0   
42                           LAWNDALE / WAYSIDE                 0.0   
43                      LAZYBROOK / TIMBERGROVE                 0.0   
44                                    MACGREGOR                 0.0   
45                                MAGNOLIA PARK                 0.0   
46                      MEADOWBROOK / ALLENDALE                 0.0   
47                          MEDICAL CENTER AREA                 0.0   
48                                     MEMORIAL                 0.0   
49                               MEYERLAND AREA                 0.0   
50                                     MID WEST                 0.0   
51                                      MIDTOWN                 0.0   
52                                  MUSEUM PARK                 0.0   
53                               NEAR NORTHSIDE                 0.0   
54                          NEARTOWN - MONTROSE                 0.0   
55                                   NORTHSHORE                 

In [41]:
#houston_grouped.head()
# set number of clusters
# set number of clusters
kclusters = 5

houston_grouped_clustering = houston_housing2.drop('SNBNAME', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(houston_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:] 



array([4, 4, 1, 4, 4, 3, 1, 3, 3, 2, 2, 1, 3, 0, 0, 4, 4, 4, 4, 0, 3, 3,
       2, 0, 4, 2, 2, 4, 2, 3, 0, 1, 2, 0, 2, 3, 3, 0, 0, 1, 0, 0, 0, 3,
       4, 0, 4, 3, 2, 4, 1, 0, 0, 3, 2, 4, 2, 0, 0, 3, 0, 3, 1, 4, 2, 0,
       4, 4, 4, 4, 4, 4, 4, 4, 2, 3, 4, 2, 4, 0, 0])

In [42]:
neighborhoods_venues_sorted.head()

SNBNAME            1st Most Common Venue  \
0                    ACRES HOME                     Burger Joint   
1  AFTON OAKS / RIVER OAKS AREA  Southern / Soul Food Restaurant   
2                         ALIEF                             Food   
3                ASTRODOME AREA                       Food Truck   
4                      BRAEBURN                             Food   

             2nd Most Common Venue 3rd Most Common Venue  
0  Southern / Soul Food Restaurant    Chinese Restaurant  
1                     Burger Joint   American Restaurant  
2              American Restaurant                Bakery  
3                Indian Restaurant         Deli / Bodega  
4                      Pizza Place        Sandwich Place

In [43]:
houston = neighborhoods_venues_sorted.join(houston_geo.set_index('SNBNAME'), on='SNBNAME')

houston = houston.join(SUM_TotHousing.set_index('SNBNAME'), on='SNBNAME')

houston # check the last columns!


SNBNAME  \
0                                    ACRES HOME   
1                  AFTON OAKS / RIVER OAKS AREA   
2                                         ALIEF   
3                                ASTRODOME AREA   
4                                      BRAEBURN   
5                                     BRAESWOOD   
6                                    BRAYS OAKS   
7                                  BRIAR FOREST   
8                                    CARVERDALE   
9                             CENTRAL NORTHWEST   
10                            CENTRAL SOUTHWEST   
11                                   CLEAR LAKE   
12                   CLINTON PARK TRI-COMMUNITY   
13                 DENVER HARBOR / PORT HOUSTON   
14                                     DOWNTOWN   
15                                 EAST HOUSTON   
16                 EAST LITTLE YORK / HOMESTEAD   
17                         EASTEX - JENSEN AREA   
18                               EDGEBROOK AREA   
19               FAIRBANKS / NORTHWEST CROSSING   
20                              FONDREN GARDENS   
21                            FORT BEND HOUSTON   
22              GOLFCREST / BELLFORT / REVEILLE   
23                             GREATER EASTWOOD   
24                           GREATER FIFTH WARD   
25                          GREATER GREENSPOINT   
26                              GREATER HEIGHTS   
27                           GREATER HOBBY AREA   
28                               GREATER INWOOD   
29                    GREATER OST / SOUTH UNION   
30                           GREATER THIRD WARD   
31                               GREATER UPTOWN   
32                  GREENWAY / UPPER KIRBY AREA   
33             GULFGATE RIVERVIEW / PINE VALLEY   
34                                      GULFTON   
35                      HARRISBURG / MANCHESTER   
36                                HIDDEN VALLEY   
37                         INDEPENDENCE HEIGHTS   
38                             KASHMERE GARDENS   
39                                KINGWOOD AREA   
40                                 LAKE HOUSTON   
41                                     LANGWOOD   
42                           LAWNDALE / WAYSIDE   
43                      LAZYBROOK / TIMBERGROVE   
44                                    MACGREGOR   
45                                MAGNOLIA PARK   
46                      MEADOWBROOK / ALLENDALE   
47                          MEDICAL CENTER AREA   
48                                     MEMORIAL   
49                               MEYERLAND AREA   
50                                     MID WEST   
51                                      MIDTOWN   
52                                  MUSEUM PARK   
53                               NEAR NORTHSIDE   
54                          NEARTOWN - MONTROSE   
55                                   NORTHSHORE   
56                          NORTHSIDE/NORTHLINE   
57                                   PARK PLACE   
58                                   PECAN PARK   
59                           PLEASANTVILLE AREA   
60                                  SECOND WARD   
61                                    SETTEGAST   
62                                   SHARPSTOWN   
63                 SOUTH ACRES / CRESTMONT PARK   
64                       SOUTH BELT / ELLINGTON   
65                                   SOUTH MAIN   
66                                   SOUTH PARK   
67                        SPRING BRANCH CENTRAL   
68                           SPRING BRANCH EAST   
69                          SPRING BRANCH NORTH   
70                           SPRING BRANCH WEST   
71                                    SUNNYSIDE   
72                    TRINITY / HOUSTON GARDENS   
73                             UNIVERSITY PLACE   
74  WASHINGTON AVENUE COALITION / MEMORIAL PARK   
75                                   WESTBRANCH   
76                                     WESTBURY   
77                                    WESTCHASE   
78         

In [45]:
# add clustering labels
houston['Cluster Labels'] = kmeans.labels_
#print(houston['Cluster Labels'])
houston.head()

SNBNAME            1st Most Common Venue  \
0                    ACRES HOME                     Burger Joint   
1  AFTON OAKS / RIVER OAKS AREA  Southern / Soul Food Restaurant   
2                         ALIEF                             Food   
3                ASTRODOME AREA                       Food Truck   
4                      BRAEBURN                             Food   

             2nd Most Common Venue 3rd Most Common Venue   Latitude  \
0  Southern / Soul Food Restaurant    Chinese Restaurant -95.436267   
1                     Burger Joint   American Restaurant -95.435636   
2              American Restaurant                Bakery -95.586392   
3                Indian Restaurant         Deli / Bodega -95.394966   
4                      Pizza Place        Sandwich Place -95.515667   

   Longitude  SUM_TotHousing  Cluster Labels  
0  29.864097          9288.0               4  
1  29.747921          8069.0               4  
2  29.686317         35498.0               1  
3  29.687930         11311.0               4  
4  29.681566          8216.0               4

In [46]:

# create map
map_clusters = folium.Map(location=[29.6196787, -95.6349463], zoom_start=9)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for k in range(0,houston['SNBNAME'].size):
    lat=houston['Longitude'][k]
    lon=houston['Latitude'][k]
    poi=houston['SNBNAME'][k]
    cluster=houston['Cluster Labels'][k]
    
#for lat, lon, poi, cluster in zip(houston['Latitude'], houston['Longitude'], houston['Neighborhood'], houston['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [48]:
houston.loc[houston['Cluster Labels'] ==0 , houston.columns[[0] + list(range(1, houston.shape[1]))]]

SNBNAME      1st Most Common Venue  \
13      DENVER HARBOR / PORT HOUSTON                Wings Joint   
14                          DOWNTOWN               Burger Joint   
19    FAIRBANKS / NORTHWEST CROSSING       Fast Food Restaurant   
23                  GREATER EASTWOOD         Mexican Restaurant   
30                GREATER THIRD WARD       Fast Food Restaurant   
33  GULFGATE RIVERVIEW / PINE VALLEY         Mexican Restaurant   
37              INDEPENDENCE HEIGHTS        Fried Chicken Joint   
38                  KASHMERE GARDENS       Fast Food Restaurant   
40                      LAKE HOUSTON  Cajun / Creole Restaurant   
41                          LANGWOOD                Pizza Place   
42                LAWNDALE / WAYSIDE                Pizza Place   
45                     MAGNOLIA PARK         Mexican Restaurant   
51                           MIDTOWN      Vietnamese Restaurant   
52                       MUSEUM PARK                 Food Truck   
57                        PARK PLACE      Vietnamese Restaurant   
58                        PECAN PARK                Pizza Place   
60                       SECOND WARD       Fast Food Restaurant   
65                        SOUTH MAIN       Fast Food Restaurant   
79  WILLOW MEADOWS / WILLOWBEND AREA                       Food   
80                       WILLOWBROOK       Fast Food Restaurant   

        2nd Most Common Venue            3rd Most Common Venue   Latitude  \
13         Mexican Restaurant             Fast Food Restaurant -95.293949   
14         Mexican Restaurant          New American Restaurant -95.359096   
19              Deli / Bodega            Vietnamese Restaurant -95.512603   
23                 Taco Place                       Food Truck -95.333601   
30  Cajun / Creole Restaurant                      Pizza Place -95.354953   
33       Fast Food Restaurant                             Food -95.317484   
37                       Food              American Restaurant -95.396065   
38                       Food                     Burger Joint -95.322484   
40                Wings Joint                 Cuban Restaurant -95.149110   
41        Fried Chicken Joint                       Food Truck -95.490932   
42         Chinese Restaurant               Mexican Restaurant -95.306654   
45         Chinese Restaurant                             Food -95.293816   
51                 Food Truck                   Sandwich Place -95.375334   
52                       Café  Southern / Soul Food Restaurant -95.382603   
57         Mexican Restaurant               Seafood Restaurant -95.271545   
58         Mexican Restaurant                             Food -95.287175   
60               Burger Joint                       Taco Place -95.327939   
65             Breakfast Spot                             Food -95.418071   
79                 Food Truck               Mexican Restaurant -95.449731   
80         Chinese Restaurant              American Restaurant -95.543023   

    Longitude  SUM_TotHousing  Cluster Labels  
13  29.766369          5289.0               0  
14  29.756689          3664.0               0  
19  29.849347          6479.0               0  
23  29.735719          4778.0               0  
30  29.728188          5824.0               0  
33  29.706825          3950.0               0  
37  29.829166          5550.0               0  
38  29.802721          4413.0               0  
40  29.983309          5253.0               0  
41  29.826409          3066.0               0  
42  29.723172          4636.0               0  
45  29.738742          6322.0               0  
51  29.742253          5568.0               0  
52  29.725881          3123.0               0  
57  29.696043          3191.0               0  
58  29.707712          5440.0               0  
60  29.750962          5120.0               0  
65  29.672870          4464.0               0  
79  29.667265          5922.0               0  
80  29.953919          4283.0              

In [69]:
cluster0=houston.loc[houston['Cluster Labels'] ==0 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster0=cluster0.drop('2nd Most Common Venue',1)
cluster0=cluster0.drop('3rd Most Common Venue',1)
cluster0=cluster0.drop('Latitude',1)
cluster0=cluster0.drop('Longitude',1)
cluster0=cluster0.drop('SUM_TotHousing',1)
cluster00=cluster0.drop('Cluster Labels',1)
cluster00.groupby('1st Most Common Venue').count()

SNBNAME
1st Most Common Venue             
Burger Joint                     1
Cajun / Creole Restaurant        1
Fast Food Restaurant             6
Food                             1
Food Truck                       1
Fried Chicken Joint              1
Mexican Restaurant               3
Pizza Place                      3
Vietnamese Restaurant            2
Wings Joint                      1

In [78]:
cluster0=houston.loc[houston['Cluster Labels'] ==0 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster0=cluster0.drop('1st Most Common Venue',1)
cluster0=cluster0.drop('3rd Most Common Venue',1)
cluster0=cluster0.drop('Latitude',1)
cluster0=cluster0.drop('Longitude',1)
cluster0=cluster0.drop('SUM_TotHousing',1)
cluster00=cluster0.drop('Cluster Labels',1)
cluster00.groupby('2nd Most Common Venue').count()


SNBNAME
2nd Most Common Venue             
Breakfast Spot                   1
Burger Joint                     1
Café                             1
Cajun / Creole Restaurant        1
Chinese Restaurant               3
Deli / Bodega                    1
Fast Food Restaurant             1
Food                             2
Food Truck                       2
Fried Chicken Joint              1
Mexican Restaurant               4
Taco Place                       1
Wings Joint                      1

In [49]:
houston.loc[houston['Cluster Labels'] == 1, houston.columns[[0] + list(range(1, houston.shape[1]))]]

SNBNAME 1st Most Common Venue     2nd Most Common Venue  \
2            ALIEF                  Food       American Restaurant   
6       BRAYS OAKS           Pizza Place      Fast Food Restaurant   
11      CLEAR LAKE    Italian Restaurant       Japanese Restaurant   
31  GREATER UPTOWN   American Restaurant             Deli / Bodega   
39   KINGWOOD AREA    Dim Sum Restaurant          Asian Restaurant   
50        MID WEST    Mexican Restaurant  Mediterranean Restaurant   
62      SHARPSTOWN                  Food      Fast Food Restaurant   

        3rd Most Common Venue   Latitude  Longitude  SUM_TotHousing  \
2                      Bakery -95.586392  29.686317         35498.0   
6         Fried Chicken Joint -95.525802  29.654755         25068.0   
11                  Cafeteria -95.134963  29.578395         24182.0   
31                       Food -95.475614  29.756552         31563.0   
39  South American Restaurant -95.198536  30.051070         24317.0   
50                     Bakery -95.512917  29.733285         25981.0   
62      Vietnamese Restaurant -95.524952  29.703853         30285.0   

    Cluster Labels  
2                1  
6                1  
11               1  
31               1  
39               1  
50               1  
62               1

In [70]:
cluster1=houston.loc[houston['Cluster Labels'] ==1 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster1=cluster1.drop('2nd Most Common Venue',1)
cluster1=cluster1.drop('3rd Most Common Venue',1)
cluster1=cluster1.drop('Latitude',1)
cluster1=cluster1.drop('Longitude',1)
cluster1=cluster1.drop('SUM_TotHousing',1)
cluster11=cluster1.drop('Cluster Labels',1)
cluster11.groupby('1st Most Common Venue').count()

SNBNAME
1st Most Common Venue         
American Restaurant          1
Dim Sum Restaurant           1
Food                         2
Italian Restaurant           1
Mexican Restaurant           1
Pizza Place                  1

In [77]:
cluster1=houston.loc[houston['Cluster Labels'] ==1 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster1=cluster1.drop('1st Most Common Venue',1)
cluster1=cluster1.drop('3rd Most Common Venue',1)
cluster1=cluster1.drop('Latitude',1)
cluster1=cluster1.drop('Longitude',1)
cluster1=cluster1.drop('SUM_TotHousing',1)
cluster11=cluster1.drop('Cluster Labels',1)
cluster11.groupby('2nd Most Common Venue').count()


SNBNAME
2nd Most Common Venue            
American Restaurant             1
Asian Restaurant                1
Deli / Bodega                   1
Fast Food Restaurant            2
Japanese Restaurant             1
Mediterranean Restaurant        1

In [50]:
houston.loc[houston['Cluster Labels'] == 2, houston.columns[[0] + list(range(1, houston.shape[1]))]]

SNBNAME 1st Most Common Venue  \
9                             CENTRAL NORTHWEST   American Restaurant   
10                            CENTRAL SOUTHWEST            Food Truck   
22              GOLFCREST / BELLFORT / REVEILLE  Fast Food Restaurant   
25                          GREATER GREENSPOINT    Italian Restaurant   
26                              GREATER HEIGHTS           Pizza Place   
28                               GREATER INWOOD  Fast Food Restaurant   
32                  GREENWAY / UPPER KIRBY AREA        Sandwich Place   
34                                      GULFTON    Mexican Restaurant   
48                                     MEMORIAL                  Food   
54                          NEARTOWN - MONTROSE           Pizza Place   
56                          NORTHSIDE/NORTHLINE    Seafood Restaurant   
64                       SOUTH BELT / ELLINGTON    Mexican Restaurant   
74  WASHINGTON AVENUE COALITION / MEMORIAL PARK   American Restaurant   
77                                    WESTCHASE         Deli / Bodega   

        2nd Most Common Venue      3rd Most Common Venue   Latitude  \
9                  Donut Shop               Burger Joint -95.444859   
10  Latin American Restaurant        American Restaurant -95.432339   
22                Pizza Place  Latin American Restaurant -95.294512   
25                Pizza Place                 Restaurant -95.410059   
26    New American Restaurant         Mexican Restaurant -95.397350   
28         Chinese Restaurant  Cajun / Creole Restaurant -95.481183   
32         Italian Restaurant         Chinese Restaurant -95.434314   
34       Fast Food Restaurant        Fried Chicken Joint -95.481885   
48              Deli / Bodega                Pizza Place -95.584429   
54         Mexican Restaurant                 Food Truck -95.397217   
56         Mexican Restaurant                Pizza Place -95.381932   
64                Pizza Place         Tex-Mex Restaurant -95.205141   
74         Mexican Restaurant                 Taco Place -95.418402   
77                       Food       Fast Food Restaurant -95.566680   

    Longitude  SUM_TotHousing  Cluster Labels  
9   29.829097         19024.0               2  
10  29.630323         19004.0               2  
22  29.672904         17530.0               2  
25  29.940435         18633.0               2  
26  29.797332         21257.0               2  
28  29.874411         15192.0               2  
32  29.732370         15091.0               2  
34  29.713116         17283.0               2  
48  29.773037         20069.0               2  
54  29.746212         19231.0               2  
56  29.854133         18327.0               2  
64  29.608477         19643.0               2  
74  29.771182         14911.0               2  
77  29.726979         16723.0               2

In [71]:
cluster2=houston.loc[houston['Cluster Labels'] ==2 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster2=cluster2.drop('2nd Most Common Venue',1)
cluster2=cluster2.drop('3rd Most Common Venue',1)
cluster2=cluster2.drop('Latitude',1)
cluster2=cluster2.drop('Longitude',1)
cluster2=cluster2.drop('SUM_TotHousing',1)
cluster22=cluster2.drop('Cluster Labels',1)
cluster22.groupby('1st Most Common Venue').count()

SNBNAME
1st Most Common Venue         
American Restaurant          2
Deli / Bodega                1
Fast Food Restaurant         2
Food                         1
Food Truck                   1
Italian Restaurant           1
Mexican Restaurant           2
Pizza Place                  2
Sandwich Place               1
Seafood Restaurant           1

In [76]:
cluster2=houston.loc[houston['Cluster Labels'] ==2 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster2=cluster2.drop('1st Most Common Venue',1)
cluster2=cluster2.drop('3rd Most Common Venue',1)
cluster2=cluster2.drop('Latitude',1)
cluster2=cluster2.drop('Longitude',1)
cluster2=cluster2.drop('SUM_TotHousing',1)
cluster22=cluster2.drop('Cluster Labels',1)
cluster22.groupby('2nd Most Common Venue').count()


SNBNAME
2nd Most Common Venue             
Chinese Restaurant               1
Deli / Bodega                    1
Donut Shop                       1
Fast Food Restaurant             1
Food                             1
Italian Restaurant               1
Latin American Restaurant        1
Mexican Restaurant               3
New American Restaurant          1
Pizza Place                      3

In [51]:
houston.loc[houston['Cluster Labels'] == 3, houston.columns[[0] + list(range(1, houston.shape[1]))]]

SNBNAME 1st Most Common Venue  \
5                    BRAESWOOD   Fried Chicken Joint   
7                 BRIAR FOREST                  Food   
8                   CARVERDALE             BBQ Joint   
12  CLINTON PARK TRI-COMMUNITY        Breakfast Spot   
20             FONDREN GARDENS                  Food   
21           FORT BEND HOUSTON             BBQ Joint   
29   GREATER OST / SOUTH UNION          Burger Joint   
35     HARRISBURG / MANCHESTER             BBQ Joint   
36               HIDDEN VALLEY                  Food   
43     LAZYBROOK / TIMBERGROVE                  Food   
47         MEDICAL CENTER AREA   American Restaurant   
53              NEAR NORTHSIDE    Mexican Restaurant   
59          PLEASANTVILLE AREA    Mexican Restaurant   
61                   SETTEGAST                  Food   
75                  WESTBRANCH                  Café   

              2nd Most Common Venue 3rd Most Common Venue   Latitude  \
5                    Sandwich Place                  Food -95.432595   
7                       Pizza Place    Mexican Restaurant -95.574395   
8                              Food   American Restaurant -95.550278   
12  Southern / Soul Food Restaurant           Wings Joint -95.262714   
20             Fast Food Restaurant                Bakery -95.503068   
21               Seafood Restaurant                  Food -95.486898   
29              American Restaurant             BBQ Joint -95.353214   
35                   Sandwich Place    Mexican Restaurant -95.265653   
36                       Food Truck           Wings Joint -95.417324   
43             Fast Food Restaurant           Pizza Place -95.437531   
47                             Café  Fast Food Restaurant -95.393353   
53                       Food Truck                  Food -95.360912   
59                      Wings Joint      Halal Restaurant -95.275180   
61              American Restaurant           Wings Joint -95.279048   
75                    Deli / Bodega  Fast Food Restaurant -95.559613   

    Longitude  SUM_TotHousing  Cluster Labels  
5   29.692977             NaN               3  
7   29.749193             NaN               3  
8   29.855090           887.0               3  
12  29.748397          1133.0               3  
20  29.625244          1145.0               3  
21  29.593609             NaN               3  
29  29.693468             NaN               3  
35  29.718863          1046.0               3  
36  29.891505          1268.0               3  
43  29.797797             NaN               3  
47  29.708646           729.0               3  
53  29.796894             NaN               3  
59  29.777972          1350.0               3  
61  29.817209          1732.0               3  
75  29.838073          1709.0               3

In [72]:
cluster3=houston.loc[houston['Cluster Labels'] ==3 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster3=cluster3.drop('2nd Most Common Venue',1)
cluster3=cluster3.drop('3rd Most Common Venue',1)
cluster3=cluster3.drop('Latitude',1)
cluster3=cluster3.drop('Longitude',1)
cluster3=cluster3.drop('SUM_TotHousing',1)
cluster33=cluster3.drop('Cluster Labels',1)
cluster33.groupby('1st Most Common Venue').count()

SNBNAME
1st Most Common Venue         
American Restaurant          1
BBQ Joint                    3
Breakfast Spot               1
Burger Joint                 1
Café                         1
Food                         5
Fried Chicken Joint          1
Mexican Restaurant           2

In [73]:
cluster3=houston.loc[houston['Cluster Labels'] ==3 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster3=cluster3.drop('1st Most Common Venue',1)
cluster3=cluster3.drop('3rd Most Common Venue',1)
cluster3=cluster3.drop('Latitude',1)
cluster3=cluster3.drop('Longitude',1)
cluster3=cluster3.drop('SUM_TotHousing',1)
cluster33=cluster3.drop('Cluster Labels',1)
cluster33.groupby('2nd Most Common Venue').count()

SNBNAME
2nd Most Common Venue                   
American Restaurant                    2
Café                                   1
Deli / Bodega                          1
Fast Food Restaurant                   2
Food                                   1
Food Truck                             2
Pizza Place                            1
Sandwich Place                         2
Seafood Restaurant                     1
Southern / Soul Food Restaurant        1
Wings Joint                            1

In [52]:
houston.loc[houston['Cluster Labels'] == 4, houston.columns[[0] + list(range(1, houston.shape[1]))]]

SNBNAME            1st Most Common Venue  \
0                     ACRES HOME                     Burger Joint   
1   AFTON OAKS / RIVER OAKS AREA  Southern / Soul Food Restaurant   
3                 ASTRODOME AREA                       Food Truck   
4                       BRAEBURN                             Food   
15                  EAST HOUSTON             Fast Food Restaurant   
16  EAST LITTLE YORK / HOMESTEAD               Seafood Restaurant   
17          EASTEX - JENSEN AREA             Fast Food Restaurant   
18                EDGEBROOK AREA               Mexican Restaurant   
24            GREATER FIFTH WARD                             Food   
27            GREATER HOBBY AREA                       Food Truck   
44                     MACGREGOR                             Food   
46       MEADOWBROOK / ALLENDALE               Mexican Restaurant   
49                MEYERLAND AREA                      Pizza Place   
55                    NORTHSHORE             Fast Food Restaurant   
63  SOUTH ACRES / CRESTMONT PARK             Fast Food Restaurant   
66                    SOUTH PARK                      Pizza Place   
67         SPRING BRANCH CENTRAL                       Steakhouse   
68            SPRING BRANCH EAST             Fast Food Restaurant   
69           SPRING BRANCH NORTH               Mexican Restaurant   
70            SPRING BRANCH WEST             Fast Food Restaurant   
71                     SUNNYSIDE                       Restaurant   
72     TRINITY / HOUSTON GARDENS                             Food   
73              UNIVERSITY PLACE              American Restaurant   
76                      WESTBURY                      Pizza Place   
78                      WESTWOOD               Chinese Restaurant   

              2nd Most Common Venue  3rd Most Common Venue   Latitude  \
0   Southern / Soul Food Restaurant     Chinese Restaurant -95.436267   
1                      Burger Joint    American Restaurant -95.435636   
3                 Indian Restaurant          Deli / Bodega -95.394966   
4                       Pizza Place         Sandwich Place -95.515667   
15                      Pizza Place    Fried Chicken Joint -95.257753   
16                           Bakery                   Food -95.297036   
17                      Pizza Place    Fried Chicken Joint -95.342538   
18               Seafood Restaurant             Taco Place -95.227092   
24              American Restaurant    Fried Chicken Joint -95.330012   
27             Fast Food Restaurant     Mexican Restaurant -95.278045   
44                      Pizza Place              BBQ Joint -95.363256   
46                       Food Truck                 Bistro -95.246746   
49                             Café  Vietnamese Restaurant -95.477615   
55               Seafood Restaurant     Mexican Restaurant -95.220746   
63                     Burger Joint     Seafood Restaurant -95.358987   
66             Fast Food Restaurant              BBQ Joint -95.333128   
67                       Taco Place           Burger Joint -95.514277   
68               Mexican Restaurant     Chinese Restaurant -95.477236   
69                Korean Restaurant     Chinese Restaurant -95.543666   
70                      Pizza Place                 Bakery -95.560603   
71                             Food           Burger Joint -95.367446   
72        Cajun / Creole Restaurant                 Bakery -95.308015   
73               Italian Restaurant             Restaurant -95.406745   
76                             Food     Mexican Restaurant -95.482300   
78             Fast Food Restaurant     African Restaurant -95.550073   

    Longitude  SUM_TotHousing  Cluster Labels  
0   29.864097          9288.0               4  
1   29.747921          8069.0               4  
3   29.687930         11311.0               4  
4   29.681566          8216.0               4  
15  29.843108          6799.0               4  
16  29.871777          7650.0              

In [74]:
cluster4=houston.loc[houston['Cluster Labels'] ==4 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster4=cluster4.drop('2nd Most Common Venue',1)
cluster4=cluster4.drop('3rd Most Common Venue',1)
cluster4=cluster4.drop('Latitude',1)
cluster4=cluster4.drop('Longitude',1)
cluster4=cluster4.drop('SUM_TotHousing',1)
cluster44=cluster4.drop('Cluster Labels',1)
cluster44.groupby('1st Most Common Venue').count()

SNBNAME
1st Most Common Venue                   
American Restaurant                    1
Burger Joint                           1
Chinese Restaurant                     1
Fast Food Restaurant                   6
Food                                   4
Food Truck                             2
Mexican Restaurant                     3
Pizza Place                            3
Restaurant                             1
Seafood Restaurant                     1
Southern / Soul Food Restaurant        1
Steakhouse                             1

In [75]:

cluster4=houston.loc[houston['Cluster Labels'] ==4 , houston.columns[[0] + list(range(1, houston.shape[1]))]]
cluster4=cluster4.drop('1st Most Common Venue',1)
cluster4=cluster4.drop('3rd Most Common Venue',1)
cluster4=cluster4.drop('Latitude',1)
cluster4=cluster4.drop('Longitude',1)
cluster4=cluster4.drop('SUM_TotHousing',1)
cluster44=cluster4.drop('Cluster Labels',1)
cluster44.groupby('2nd Most Common Venue').count()

SNBNAME
2nd Most Common Venue                   
American Restaurant                    1
Bakery                                 1
Burger Joint                           2
Café                                   1
Cajun / Creole Restaurant              1
Fast Food Restaurant                   3
Food                                   2
Food Truck                             1
Indian Restaurant                      1
Italian Restaurant                     1
Korean Restaurant                      1
Mexican Restaurant                     1
Pizza Place                            5
Seafood Restaurant                     2
Southern / Soul Food Restaurant        1
Taco Place                             1